##**FLUJO COMPLETO DEL SISTEMA DE DETECCIÓN DE TENIS**

En este último notebook realizaremos un **flujo completo** juntando todos los elementos desarrollados durante la práctica. De esta manera podremos crear y visualizar un video entero en el que detectamos y cálculamos la posición de la pelota, los jugadores y las líneas de la pista, junto al cálculo y generación del minimapa y de la distancia recorrida por los jugadores.

In [ ]:
!pip install ultralytics
from ultralytics import YOLO

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 79.6 MB/s eta 0:00:00
Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


In [ ]:
from google.colab import drive
import sys

drive.mount('/content/drive')
sys.path.append('/content/drive/MyDrive/tenis_functions')

Mounted at /content/drive


In [ ]:
!mkdir -p ~/.kaggle

!cp /content/drive/MyDrive/dataset_tennis/kaggle.json ~/.kaggle/

!chmod 600 ~/.kaggle/kaggle.json

!kaggle datasets download -d sofuskonglevoll/tracknet-tennis -p data

Dataset URL: https://www.kaggle.com/datasets/sofuskonglevoll/tracknet-tennis
License(s): unknown
 98% 2.33G/2.39G [00:05<00:00, 169MB/s] 
100% 2.39G/2.39G [00:05<00:00, 439MB/s]


In [ ]:
!mkdir -p data/tracknet
!unzip -q -o data/tracknet-tennis.zip -d data/tracknet

### **BIBLIOTECAS Y FUNCIONES AUXILIARES**
Se cargan todas las **funciones de los otros notebooks** que hemos ido desarrollando. Para ello hemos introducido las funciones necesarias en distintos ficheros para poder importarlas y facilitar la lectura del notebook.

In [ ]:
from court_functions import *
from player_map_functions import *
from detect_players_functions import *
from tracknet_functions import *

import matplotlib.pyplot as plt
import numpy as np
import cv2
import glob
import torch
from google.colab.patches import cv2_imshow
import itertools
import random
from IPython.display import Video, display
import os

La función `calcular_distancias_acumuladas()` se encarga de **estimar la distancia recorrida por cada jugador** a lo largo del vídeo. Para ello, primero calcula una **referencia de escala en píxeles** a partir de la **altura de las bounding boxes** de cada jugador, que permite **convertir desplazamientos en imagen a distancias relativas**. A continuación, **interpola las posiciones** (`interpola_posiciones()`) de los jugadores entre fotogramas para **corregir posibles pérdidas de detección**. Finalmente, a partir de estas trayectorias suavizadas y de la referencia de escala, **calcula y acumula la distancia recorrida** por cada jugador frame a frame, devolviendo la distancia acumulada total para ambos.

In [ ]:
def calcular_distancias_acumuladas(datos_trackeo):
    # Calcular referencias de altura
    top_ref_altura_px = calcula_ref_altura_px(datos_trackeo, "top_bbox")
    bottom_ref_altura_px = calcula_ref_altura_px(datos_trackeo, "bottom_bbox")

    # Interpolar posiciones
    top_interp = interpola_posiciones(datos_trackeo, "top_player")
    bottom_interp = interpola_posiciones(datos_trackeo, "bottom_player")

    # Calcular distancias acumuladas
    top_dist_acumulada = calcula_distancia_acumulada(top_interp, top_ref_altura_px)
    bottom_dist_acumulada = calcula_distancia_acumulada(bottom_interp, bottom_ref_altura_px)

    return top_dist_acumulada, bottom_dist_acumulada

## **FUNCIONES PARA EL PIPELINE FINAL**

Para generar el video con todas las detecciones vamos a definir **3 funciones** que nos realizaran el proceso entero llamando a las funciones explicadas en los notebooks anteriores.

La función `recopilar_datos_trackeo()` se encarga de **recopilar y estructurar la información necesaria** para el **seguimiento temporal** de los jugadores a lo largo del vídeo. Para cada fotograma, se calcula periódicamente la **homografía** de la pista y **detecta a los jugadores mediante YOLO**. A partir de las bounding boxes detectadas, se **estima la posición de contacto con el suelo** de cada jugador y los **asigna de forma consistente a jugador superior e inferior** utilizando la geometría de la pista y la homografía. Finalmente, almacena **para cada frame las posiciones y las bounding boxes asociadas**, incluso en aquellos casos en los que la detección no es válida, generando una secuencia temporal coherente que sirve como base para el cálculo posterior de la distancia recorrida.

In [ ]:
def recopilar_datos_trackeo(img_paths, modelo, detector, court_points, recalc_num_frames=7):
    datos_trackeo = []

    court_keypoints = None
    H = None

    for frame_idx, img_path in enumerate(img_paths):
        img = cv2.imread(img_path)
        img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)

        frame_info = {
            "frame_idx": frame_idx,
            "top_player": None,
            "bottom_player": None,
            "top_bbox": None,
            "bottom_bbox": None
        }

        if frame_idx % recalc_num_frames == 0 or court_keypoints is None or H is None:
            try:
                _, court_keypoints, H = process_court_image(img_path, detector)
            except Exception:
                H = None
                court_keypoints = None

        if H is None or court_keypoints is None:
            datos_trackeo.append(frame_info)
            continue

        predicciones = modelo(img_rgb, conf=0.4, classes=[0], verbose=False)

        bboxes_players = []
        for r in predicciones:
            for bbox in r.boxes:
                x1, y1, x2, y2 = bbox.xyxy[0].cpu().numpy()

                bboxes_players.append({
                    "bbox": [int(x1), int(y1), int(x2), int(y2)]
                })

        if len(bboxes_players) < 2:
            datos_trackeo.append(frame_info)
            continue

        for bb in bboxes_players:
            bb["x_c"], bb["y_c"] = bbox_center_pies(bb["bbox"])

        kp_top_court, kp_bottom_court = kp_virtuales(court_points)

        top_player, bottom_player = asigna_jugadores_por_pies(
            bboxes_players, kp_top_court, kp_bottom_court, H
        )

        if top_player is not None:
            frame_info["top_player"] = (top_player["x_c"], top_player["y_c"])
            frame_info["top_bbox"] = top_player["bbox"]

        if bottom_player is not None:
            frame_info["bottom_player"] = (bottom_player["x_c"], bottom_player["y_c"])
            frame_info["bottom_bbox"] = bottom_player["bbox"]

        datos_trackeo.append(frame_info)

    return datos_trackeo



---



Esta función se encarga de **generar el vídeo final** del análisis, integrando en un único flujo todos los módulos desarrollados previamente en los distintos notebooks. A lo largo de la secuencia de imágenes, se van **aplicando de forma coordinada los procesos de detección de la pista, detección y asignación de jugadores, seguimiento de la pelota y visualización de métricas**.

En cada fotograma, la función **recalcula periódicamente los keypoints** de la pista y la homografía para **mantener una correspondencia geométrica** estable entre la imagen y el plano real de la pista. A continuación, se vuelven a  detectar los jugadores mediante YOLO, se estiman sus posiciones sobre el plano del suelo y se asignan de forma consistente a jugador superior e inferior. Estas **posiciones** se transforman **al sistema de coordenadas de la pista** para su posterior representación en el minimapa.

De manera paralela, se incorpora la **trayectoria de la pelota** previamente estimada, dibujando tanto su **posición actual como su estela temporal**. Sobre la imagen original se superponen las **distintas capas de información: keypoints de la pista, modelo geométrico proyectado, bounding boxes de los jugadores, contorno de la pista, minimapa y HUD con las distancias acumuladas.** Finalmente, cada fotograma procesado se escribe en el vídeo de salida, dando lugar a una visualización completa que combina detección, seguimiento y análisis geométrico en un único resultado coherente.

In [ ]:
def renderiza_video_final(img_paths, out_path, modelo, detector, court_ref_img,
                          court_points, dims, top_dist_acumulada, bottom_dist_acumulada, ball_positions, fps=30, recalc_num_frames=7,
                          minicourt_scale=0.28):
    H_img, W_img = dims
    fourcc = cv2.VideoWriter_fourcc(*"mp4v")
    video_writer = cv2.VideoWriter(out_path, fourcc, fps, (W_img, H_img))

    court_keypoints = None
    H = None

    ball_trail = deque(maxlen=8) # se guarda la estela de la pelota

    for frame_idx, img_path in enumerate(img_paths):
        # cargado de imagenes
        img = cv2.imread(img_path)
        img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
        img_out = img.copy()

        # se actualizan y refinan los kps y se calcula la homografia cada N frames
        if frame_idx % recalc_num_frames == 0 or court_keypoints is None or H is None:
            try:
                _, court_keypoints, H = process_court_image(img_path, detector)
            except Exception:
                H = None
                court_keypoints = None

        if H is None or court_keypoints is None:
            video_writer.write(img)
            continue

        # predicciones con YOLO
        predicciones = modelo(img_rgb, conf=0.4, classes=[0], verbose=False)

        bboxes_players = []
        for r in predicciones:
            for bbox in r.boxes:
                x1, y1, x2, y2 = bbox.xyxy[0].cpu().numpy()
                conf = float(bbox.conf[0].cpu().numpy())

                bboxes_players.append({
                    "bbox": [int(x1), int(y1), int(x2), int(y2)],
                    "conf": conf
                })

        if len(bboxes_players) < 2:
            video_writer.write(img_out)
            continue

        # se calcula el centro estimado de los pies para cada persona
        for bb in bboxes_players:
            bb["x_c"], bb["y_c"] = bbox_center_pies(bb["bbox"])

        # keypoints virtuales
        kp_top_court, kp_bottom_court = kp_virtuales(court_points)

        # asignacion de jugadores por los pies
        top_player, bottom_player = asigna_jugadores_por_pies(
            bboxes_players, kp_top_court, kp_bottom_court, H
        )

        # transformacion de coordenadas a plano pista
        if top_player is None or bottom_player is None:
            top = [-100, -100]
            bottom = [-100, -100]
        else:
            top = image_to_court(
                np.array([top_player["x_c"], top_player["y_c"]], dtype=np.float32),
                h_inv(H)
            )
            bottom = image_to_court(
                np.array([bottom_player["x_c"], bottom_player["y_c"]], dtype=np.float32),
                h_inv(H)
            )

        # --- dibujado ---

        # keypoints reales
        img_out = detector.draw_keypoints(img_out, court_keypoints.reshape(-1))

        # overlay de la pista
        img_out = overlay_court(image=img, court_ref=court_ref_img, H=H)

        # bounding boxes
        img_out = dibuja_bbox_jugadores(img_out, top_player, bottom_player)

        # bordes de la pista
        border_pts = get_court_border(court_ref_img)
        border_img_pts = project_court_border(border_pts, H)
        img_out = draw_court_border(
            img_out, border_img_pts, color=(0, 255, 255), thickness=4
        )

        # overlay de la pelota
        ball_pos = ball_positions[frame_idx]
        img_out = draw_ball_and_trail(img_out, ball_pos, ball_trail)

        # mini-court view
        img_out = draw_minicourt_overlay(
            image=img_out,
            court_ref=court_ref_img,
            player_positions_court=[top, bottom],
            scale=minicourt_scale
        )

        # HUD de distancias
        idx = min(frame_idx, len(top_dist_acumulada) - 1)
        img_out = dibuja_hud(
            top_dist_acumulada[idx],
            bottom_dist_acumulada[idx],
            img_out
        )

        video_writer.write(img_out)

    video_writer.release()
    print(f"Vídeo generado: {out_path}")



La función `analizar_tenis_clip()` actúa como **orquestador principal de todo el sistema** de análisis del partido de tenis, integrando en un **único flujo** los distintos módulos desarrollados previamente para detección, seguimiento y visualización.

En primer lugar, se inicializan los modelos necesarios: YOLO para la detección de jugadores y el detector de líneas de pista para la estimación de los keypoints y la homografía. A continuación, se cargan todas las imágenes del clip y se obtiene su resolución, que se utilizará para generar correctamente el vídeo de salida. También se crea el modelo geométrico de referencia de la pista, junto con sus puntos clave en coordenadas reales.

Una vez preparado el contexto, la función recopila la información de seguimiento de los jugadores a lo largo de todo el clip mediante `recopilar_datos_trackeo`. A partir de estos datos, se calculan las distancias acumuladas recorridas por cada jugador, que posteriormente se mostrarán en el HUD del vídeo. De forma paralela, se obtiene la trayectoria de la pelota frame a frame utilizando el modelo TrackNet, encapsulada en la función `tracknet_ball_trajectory`, que devuelve una trayectoria limpia y suavizada.

Finalmente, toda esta información se combina en la llamada a `renderiza_video_final`, donde se generan los fotogramas finales del vídeo: se proyecta la pista sobre la imagen, se dibujan los jugadores, la pelota y su estela, el minimapa y las métricas de distancia. El resultado es un vídeo completo que integra detección, seguimiento y análisis geométrico de forma coherente. La función devuelve la ruta del vídeo generado como salida final del proceso.

In [ ]:
def analizar_tenis_clip(img_dir, out_path, tracknet_model, fps=30,
                        recalc_num_frames=7, minicourt_scale=0.28):

    modelo = YOLO("yolov8x")
    detector = CourtLineDetector("drive/MyDrive/model_court.pth")

    img_paths = sorted(glob.glob(os.path.join(img_dir, "*.jpg")))

    if len(img_paths) == 0:
        raise ValueError("No se encontraron imágenes en el directorio")

    first_img = cv2.imread(img_paths[0])
    H_img, W_img = first_img.shape[:2]

    # se genera la pista de referencia
    court_ref_img, court_points = create_tennis_court_reference()

    datos_trackeo = recopilar_datos_trackeo(img_paths, modelo, detector, court_points, recalc_num_frames)
    top_dist_acumulada, bottom_dist_acumulada = calcular_distancias_acumuladas(datos_trackeo)

    # se obtienen las posiciones de la pelota en cada frame

    ball_positions = tracknet_ball_trajectory(
                    img_paths=img_paths,
                    model=tracknet_model
                )

    renderiza_video_final(img_paths, out_path, modelo, detector, court_ref_img, court_points, (H_img, W_img),
                          top_dist_acumulada, bottom_dist_acumulada, ball_positions)

    return out_path

In [ ]:
# cargo el modelo de tracknet

# ruta del modelo en Drive
MODEL_PATH = "/content/drive/My Drive/TrackNet_Models/TrackNet_RGB_A100_Final.pth"

# GPU
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# (asumimos que la clase TrackNet ya está definida en una celda anterior)
tracknet_model = TrackNet(in_ch=9, base_ch=64).to(device)
tracknet_model.load_state_dict(torch.load(MODEL_PATH, map_location=device))
tracknet_model.eval()

TrackNet(
  (down1): ConvBlock(
    (conv1): Conv2d(9, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  )
  (pool1): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (down2): ConvBlock(
    (conv1): Conv2d(64, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (bn1): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (conv2): Conv2d(128, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (bn2): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  )
  (pool2): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (down3): ConvBlock(
    (conv1): Conv2d(128, 256, kernel_size=(3, 3), stride=(1,

Con esta simple llamada realizamos el proceso completo de detección y creación del video.

In [ ]:
out_path = analizar_tenis_clip(img_dir="data/tracknet/Dataset/game7/Clip4", out_path="out_path.mp4", tracknet_model = tracknet_model)

Analizando trayectoria


  0%|          | 0/901 [00:00<?, ?it/s]

Vídeo generado: out_path.mp4


Finalmente visualizamos el video generado.

In [ ]:
!ffmpeg -y -i out_path.mp4 -vcodec libx264 -pix_fmt yuv420p out_path_fixed.mp4 > /dev/null 2>&1

display(Video("out_path_fixed.mp4", embed=True))